# Assignment 1


In [1]:
import numpy as np
np.random.seed(13) #TODO Check if this is used for sgd
import keras.backend as K
from keras.models import Sequential
from keras.layers import Dense, Embedding, Reshape, Lambda
from keras.utils import np_utils
from keras.utils.data_utils import get_file
from keras.preprocessing.text import Tokenizer
from keras.utils.vis_utils import model_to_dot
from keras.preprocessing import sequence
from gensim.models import KeyedVectors
from sklearn.manifold import TSNE
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.neighbors import NearestNeighbors as nn
from matplotlib import pylab
from __future__ import division

Using TensorFlow backend.
c:\program files\python\lib\site-packages\gensim\utils.py:862: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [2]:
# DO NOT Modify the lines in this cell
path = 'alice.txt'
corpus = open(path).readlines()[0:700]

corpus = [sentence for sentence in corpus if sentence.count(" ") >= 2]

tokenizer = Tokenizer(filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n'+"'")
tokenizer.fit_on_texts(corpus)
corpus = tokenizer.texts_to_sequences(corpus)
nb_samples = sum(len(s) for s in corpus)
V = len(tokenizer.word_index) + 1

# Is this something they need to change?
dim = 100
window_size = 2 #use this window size for Skipgram, CBOW, and the model with the additional hidden layer
window_size_corpus = 4 #use this window size for the co-occurrence matrix

## Question 1

### Co-occurrence Matrix
Use the provided code to load the "Alice in Wonderland" text document. 
1. Implement the word-word co-occurrence matrix for “Alice in Wonderland”
2. Normalize the words such that every value lies within a range of 0 and 1
3. Compute the cosine distance between the given words:
    - Alice 
    - Dinah
    - Rabbit
4. List the 5 closest words to 'Alice'. Discuss the results.
5. Discuss what the main drawbacks are of a term-term co-occurence matrix solutions?


In [3]:
#create co-occurrence matrix
matrix = np.zeros((V,V), dtype=float)
a = 0
maximum = 0.0
for sentence in corpus:
    for index, word in enumerate(sentence):
        j = 1
        while j <= window_size_corpus:
            if index + j < len(sentence) and sentence[index + j] != word:
                matrix[word][sentence[index + j]] = matrix[word][sentence[index + j]] + 1
                if matrix[word][sentence[index + j]] > maximum:
                    maximum = matrix[word][sentence[index + j]]
            if index - j >= 0 and sentence[index - j] != word:
                matrix[word][sentence[index - j]] = matrix[word][sentence[index - j]] + 1
                if matrix[word][sentence[index - j]] > maximum:
                    maximum = matrix[word][sentence[index - j]]
            j = j + 1

            
#normalize all words
for x in range(V):
    for y in range(V):
        matrix[x][y] = float(matrix[x][y]) / float(maximum)
        
f = open('vectors_co_occurrence.txt',"w")
f.write(" ".join([str(V - 1),str(V)]))
f.write("\n")

#vectors = your word co-occurrence matrix
vectors = []
for word, i in tokenizer.word_index.items():    
    f.write(word)
    f.write(" ")
    f.write(" ".join(map(str, matrix[i])))
    f.write("\n")
f.close()

matrix

array([[ 0.        ,  0.        ,  0.        , ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.93421053, ...,  0.01315789,
         0.        ,  0.        ],
       [ 0.        ,  0.93421053,  0.        , ...,  0.01315789,
         0.01315789,  0.01315789],
       ..., 
       [ 0.        ,  0.01315789,  0.01315789, ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.01315789, ...,  0.        ,
         0.        ,  0.        ],
       [ 0.        ,  0.        ,  0.01315789, ...,  0.        ,
         0.        ,  0.        ]])

In [18]:
#find cosine similarity to Alice, Dinah and Rabbit
alice_index = tokenizer.word_index["alice"]
dinah_index = tokenizer.word_index["dinah"]
rabbit_index = tokenizer.word_index["rabbit"]

co_occurrence = KeyedVectors.load_word2vec_format('./vectors_co_occurrence.txt', binary=False)
print("Alice and rabbit", co_occurrence.similarity("alice", "rabbit"))
print("Alice and dinah", co_occurrence.similarity("alice", "dinah"))
print("Rabbit and dinah", co_occurrence.similarity("rabbit", "dinah"))



Alice and rabbit 0.0763040757575
Alice and dinah 0.148538650058
Rabbit and dinah 0.0810361087


In [19]:
#find the closest words to Alice
co_occurrence = KeyedVectors.load_word2vec_format('./vectors_co_occurrence.txt', binary=False)
co_occurrence.similar_by_word("alice", 5)

c:\program files\python\lib\site-packages\gensim\models\keyedvectors.py:829: RuntimeWarning: invalid value encountered in true_divide
  self.syn0norm = (self.syn0 / sqrt((self.syn0 ** 2).sum(-1))[..., newaxis]).astype(REAL)


[('ahem', 0.5704826712608337),
 ('ugh', 0.5704826712608337),
 ('she', 0.5335381031036377),
 ('say', 0.5302320122718811),
 ('listen', 0.49875974655151367)]

Discussion of the drawbacks:

In [7]:
#Save your all the vector representations of your word embeddings in this way
#Change when necessary the sizes of the vocabulary/embedding dimension

f = open('vectors_co_occurrence.txt',"w")
#f.write(" ".join([str(V - 1),str(V - 1)]))
f.write(" ".join([str(V - 1),str(V)]))
f.write("\n")

#vectors = your word co-occurrence matrix
vectors = []
for word, i in tokenizer.word_index.items():    
    f.write(word)
    f.write(" ")
    f.write(" ".join(map(str, matrix[i])))
    #f.write(" ".join(map(str, list(vectors[i,:]))))
    f.write("\n")
f.close()

In [52]:
#reopen your file as follows

co_occurrence = KeyedVectors.load_word2vec_format('./vectors_co_occurrence.txt', binary=False)

## Question 2

### Word embeddings
Build embeddings with a keras implementation where the embedding vector is of length 50, 150 and 300. Use the Alice in Wonderland text book for training.
1. Using the CBOW model
2. Using Skipgram model
3. Add extra hidden dense layer to CBow and Skipgram implementations. Choose an activation function for that layer and justify your answer.
4. Analyze the four different word embeddings
    - Implement your own function to perform the analogy task with. Do not use existing libraries for this task such as Gensim. Your function should be able to answer whether an anaology as in the example given in the pdf-file is true.
    - Compare the performance on the analogy task between the word embeddings that you have trained in 2.1, 2.2 and 2.3.  
    - Visualize your results and interpret your results
5. Use the word co-occurence matrix from Question 1. Compare the performance on the analogy task with the performance of your trained word embeddings.  
6. Discuss:
    - What are the main advantages of CBOW and Skipgram?
    - What is the advantage of negative sampling?
    - What are the main drawbacks of CBOW and Skipgram?
7. Load pre-trained embeddings on large corpuses (see the pdf file). You only have to consider the word embeddings with an embedding size of 300
    - Compare performance on the analogy task with your own trained embeddings from "Alice in Wonderland". You can limit yourself to the vocabulary of Alice in Wonderland. Visualize the pre-trained word embeddings and compare these with the results of your own trained word embeddings. 


In [45]:
#prepare data for cbow

# link: http://www.claudiobellei.com/2018/01/07/backprop-word2vec-python/

def to_categorical(y, num_classes=None):
    """Converts a class vector (integers) to binary class matrix.
    E.g. for use with categorical_crossentropy.
    # Arguments
        y: class vector to be converted into a matrix
            (integers from 0 to num_classes).
        num_classes: total number of classes.
    # Returns
        A binary matrix representation of the input.
    """
    y = np.array(y, dtype='int')
    input_shape = y.shape
    if input_shape and input_shape[-1] == 1 and len(input_shape) > 1:
        input_shape = tuple(input_shape[:-1])
    y = y.ravel()
    if not num_classes:
        num_classes = np.max(y) + 1
    n = y.shape[0]
    categorical = np.zeros((n, num_classes))
    categorical[np.arange(n), y] = 1
    output_shape = input_shape + (num_classes,)
    categorical = np.reshape(categorical, output_shape)
    return categorical

def corpus2io(corpus_tokenized, V, window_size):
    """Converts corpus text into context and center words
    # Arguments
        corpus_tokenized: corpus text
        window_size: size of context window
    # Returns
        context and center words (arrays)
    """
    for words in corpus_tokenized:
        L = len(words)
        for index, word in enumerate(words):
            contexts = []
            labels = []
            s = index - window_size
            e = index + window_size + 1
            contexts.append([words[i]-1 for i in range(s, e) if 0 <= i < L and i != index])
            labels.append(word-1)
            x = np_utils.to_categorical(contexts, V)
            y = np_utils.to_categorical(labels, V)
            yield (x, y.ravel())

In [52]:
#create CBOW model
def softmax(x):
    """Calculate softmax based probability for given input vector
    # Arguments
        x: numpy array/list
    # Returns
        softmax of input array
    """
    e_x = np.exp(x - np.max(x))
    return e_x / e_x.sum(axis=0)

def cbow(context, label, W1, W2, loss):
    """
    Implementation of Continuous-Bag-of-Words Word2Vec model
    :param context: all the context words (these represent the inputs)
    :param label: the center word (this represents the label)
    :param W1: weights from the input to the hidden layer
    :param W2: weights from the hidden to the output layer
    :param loss: float that represents the current value of the loss function
    :return: updated weights and loss
    """
    x = np.mean(context, axis=0)
    h = np.dot(W1.T, x)
    u = np.dot(W2.T, h)
    y_pred = softmax(u)
    e = -label + y_pred
    dW2 = np.outer(h, e)
    dW1 = np.outer(x, np.dot(W2, e))
    new_W1 = W1 - eta * dW1
    new_W2 = W2 - eta * dW2
    loss += -float(u[label == 1]) + np.log(np.sum(np.exp(u)))
    return new_W1, new_W2, loss

In [6]:
#define loss function
#cbow.compile(loss='categorical_crossentropy', optimizer='adadelta')

In [55]:
#train model
np.random.seed(100)
N = 2
#learning rate
eta = 0.1 
W1 = np.random.rand(V, N)
W2 = np.random.rand(N, V)
loss = 0.
for i, (context, label) in enumerate(corpus2io(corpus, V, window_size)):
    W1, W2, loss = cbow(context, label, W1, W2, loss)
    print("Training example #{} \n-------------------- \n\n \t label = {}, \n \t context = {}".format(i, label, context))
    print("\t W1 = {}\n\t W2 = {} \n\t loss = {}\n".format(W1, W2, loss))

Training example #0 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ 0.54340494  0.27836939]
 [ 0.42451759  0.84477613]
 [ 0.00471886  0.12156912]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.52159879  0.63359085]]
	 W2 = [[ 0.35423324  0.37419378  0.22849334 ...,  0.09387946  0.63660916
   0.41018209]
 [ 0.75476828  0.51239142  0.69479456 ...,  0.37792837  0.54067982
   0.8477183 ]] 
	 loss = 7.531115795719348

Training example #1 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 1.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ 0.53966931  0.27232278]
 [ 0.42451759  0.84477613]
 [ 0.00471886  0.12156912]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.52159879  0.63359085]]
	 W2 = [[ 0.35418879  0.37415312  0.22845274 ...,  0.09384625  0.63656196
   0.41

Training example #67 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ 0.5380906   0.27574086]
 [ 0.42458444  0.85631231]
 [ 0.00321838  0.09631677]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.52159879  0.63359085]]
	 W2 = [[ 0.5471338   0.47028416  0.30726716 ...,  0.09189373  0.63371905
   0.40714941]
 [ 0.95731842  0.66163642  0.78073014 ...,  0.37567307  0.53744857
   0.84421808]] 
	 loss = 481.36893693257383

Training example #68 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ 0.5380906   0.27574086]
 [ 0.42458444  0.85631231]
 [ 0.00321838  0.09631677]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.52159

Training example #122 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ 0.47272848  0.25804448]
 [ 0.40498466  0.81908467]
 [ 0.00321838  0.09631677]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.52159879  0.63359085]]
	 W2 = [[ 0.70781828  0.57731205  0.3051451  ...,  0.09029312  0.63147079
   0.40485668]
 [ 1.14272125  0.71693576  0.77865181 ...,  0.37411099  0.53530283
   0.84197913]] 
	 loss = 872.405679166699

Training example #123 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ 0.47272848  0.25804448]
 [ 0.40498466  0.81908467]
 [ 0.00321838  0.09631677]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.52159

 [ 0.  0.  1. ...,  0.  0.  0.]]
	 W1 = [[ 0.44629426  0.29326907]
 [ 0.40498466  0.81908467]
 [ 0.0238343   0.14839228]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.52159879  0.63359085]]
	 W2 = [[ 0.7765716   0.57560708  0.44083213 ...,  0.08916205  0.6298752
   0.40318568]
 [ 1.23318692  0.7149786   0.91931175 ...,  0.3727933   0.53348287
   0.84004118]] 
	 loss = 1168.2351390616357

Training example #165 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  1. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ 0.44629426  0.29326907]
 [ 0.40498466  0.81908467]
 [ 0.01037954  0.14018073]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.52159879  0.63359085]]
	 W2 = [[ 0.77653283  0.575578    0.44080166 ...,  0.0891405   0.62984785
   0.40315658]
 [ 1.23313293  0.71493809  0.9192693  ...,  0.37276329  0.53344479
   0.84000065]] 
	 loss 

Training example #193 
-------------------- 

 	 label = [ 0.  1.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ 0.44436445  0.33078452]
 [ 0.41136684  0.79399003]
 [ 0.00614375  0.1242597 ]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.52159879  0.63359085]]
	 W2 = [[ 0.88113771  0.6310732   0.49016113 ...,  0.0882919   0.62865252
   0.40195393]
 [ 1.2858622   0.74722847  0.97714944 ...,  0.3720266   0.53242705
   0.83894878]] 
	 loss = 1372.512167680139

Training example #194 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  1.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ 0.44436445  0.33078452]
 [ 0.41771573  0.80359413]
 [ 0.00614375  0.1242597 ]
 ..., 
 [ 0.95567362  0.0367942 ]
 [ 0.24258509  0.61645125]
 [ 0.5215

...

 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6269 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  1.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6270 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan 

 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6324 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6325 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan 

Training example #6388 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 1.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6389 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 1.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6390 
-------------------- 

 	 label = [ 1.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan

 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6461 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6462 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan

	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6534 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan  nan ...,  nan  nan  nan]] 
	 loss = nan

Training example #6535 
-------------------- 

 	 label = [ 0.  0.  0. ...,  0.  0.  0.], 
 	 context = [[ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]
 [ 0.  0.  0. ...,  0.  0.  0.]]
	 W1 = [[ nan  nan]
 [ nan  nan]
 [ nan  nan]
 ..., 
 [ nan  nan]
 [ nan  nan]
 [ nan  nan]]
	 W2 = [[ nan  nan  nan ...,  nan  nan  nan]
 [ nan  nan 

In [39]:
#prepare data for Skipgram

        


In [44]:
#create Skipgram model
data, labels = sequence.skipgrams(corpus, V, window_size=window_size, negative_samples=1., shuffle=True, categorical=False, sampling_table=None)

co_occurrence = KeyedVectors.load_word2vec_format('./vectors_co_occurrence.txt', binary=False)
co_occurrence

TypeError: 'int' object is not iterable

In [ ]:
#define loss function for Skipgram


In [32]:
#train Skipgram model
for ite in range(10):
    onehot = np.zeros(V, dtype=int)
    randomword = np.random.randint(V, size=1)[0]
    onehot[randomword] = 1


[0 0 0 ..., 0 0 0]
[0 0 0 ..., 0 0 0]
[0 0 0 ..., 0 0 0]
[0 0 0 ..., 0 0 0]
[0 0 0 ..., 0 0 0]
[0 0 0 ..., 0 0 0]
[0 0 0 ..., 0 0 0]
[0 0 0 ..., 0 0 0]
[0 0 0 ..., 0 0 0]
[0 0 0 ..., 0 0 0]


In [15]:
#create CBOW model with additional dense layer


In [16]:
#define loss function for CBOW + dense


In [17]:
#train model for CBOW + dense


In [ ]:
#create Skipgram with additional dense layer


In [ ]:
#define loss function for Skipgram + dense


In [ ]:
#train model for Skipgram + dense


In [ ]:
#Implement your own analogy function


Comparison performance:

In [ ]:
#Visualization results trained word embeddings


Interpretation results of the visualization

Compare the results of the trained word embeddings with the word-word co-occurrence matrix

Discussion of the advantages of CBOW and Skipgram, the advantages of negative sampling and drawbacks of CBOW and Skipgram

In [ ]:
#load pretrained word embeddings of word2vec

path_word2vec = "your path /GoogleNews-vectors-negative300.bin"

word2vec = KeyedVectors.load_word2vec_format(path, binary=True)

In [ ]:
#load pretraind word embeddings of Glove

path = "your path /glove.6B/glove.6B.300d_converted.txt"

#convert GloVe into word2vec format
gensim.scripts.glove2word2vec.get_glove_info(path)
gensim.scripts.glove2word2vec.glove2word2vec(path, "glove_converted.txt")

glove = KeyedVectors.load_word2vec_format(path, binary=False)

In [ ]:
#Visualize the pre-trained word embeddings

Comparison performance with your own trained word embeddings